In [14]:
import json
import requests
import time
import collections
import numpy as np
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Embedding, Dropout, Bidirectional, Conv1D
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical

class HangmanAPI:
    def __init__(self, access_token=None, session=None, timeout=None):
        self.hangman_url = self.determine_hangman_url()
        self.access_token = access_token
        self.session = session or requests.Session()
        self.timeout = timeout
        self.guessed_letters = []
        self.incorrect_guesses = set()
        self.guessed = set()

        # Load the dictionary
        full_dictionary_location = "/content/words_250000_train.txt"
        self.full_dictionary = self.build_dictionary(full_dictionary_location)
        self.full_dictionary_common_letter_sorted = self.get_common_letter_sorted(self.full_dictionary)
        self.letter_set = sorted(set("".join(self.full_dictionary)))
        self.probabilities = [0] * len(self.letter_set)

        # Build n-gram models
        self.unigram, self.bigram, self.trigram, self.fourgram, self.fivegram = self.build_ngram_models(self.full_dictionary)

        # Initialize the Enhanced Deep Learning model
        self.char_to_int, self.int_to_char, self.model = self.build_enhanced_lstm_model(self.full_dictionary)
        self.max_word_length = 32  # Assuming a maximum word length

    def get_common_letter_sorted(self, dictionary):
        # Count letter frequencies in the entire dictionary
        letter_counts = collections.Counter("".join(dictionary))
        # Sort letters by frequency, most common first
        return sorted(letter_counts.items(), key=lambda x: x[1], reverse=True)


    def build_dictionary(self, dictionary_file_location):
        with open(dictionary_file_location, "r") as text_file:
            return text_file.read().splitlines()

    @staticmethod
    def determine_hangman_url():
        links = ['https://trexsim.com', 'https://sg.trexsim.com']
        response_times = {}
        for link in links:
            start = time.time()
            requests.get(link)
            response_times[link] = time.time() - start
        best_link = min(response_times, key=response_times.get)
        return f'{best_link}/trexsim/hangman'

    def build_ngram_models(self, dictionary):
        unigram = collections.defaultdict(lambda: collections.defaultdict(int))
        bigram = collections.defaultdict(lambda: collections.defaultdict(lambda: collections.defaultdict(int)))
        trigram = collections.defaultdict(lambda: collections.defaultdict(lambda: collections.defaultdict(int)))
        fourgram = collections.defaultdict(lambda: collections.defaultdict(lambda: collections.defaultdict(lambda: collections.defaultdict(int))))
        fivegram = collections.defaultdict(lambda: collections.defaultdict(lambda: collections.defaultdict(lambda: collections.defaultdict(lambda: collections.defaultdict(int)))))

        for word in dictionary:
            for i in range(len(word) - 4):
                bigram[len(word)][word[i]][word[i+1]] += 1
                trigram[word[i]][word[i+1]][word[i+2]] += 1
                fourgram[word[i]][word[i+1]][word[i+2]][word[i+3]] += 1
                fivegram[word[i]][word[i+1]][word[i+2]][word[i+3]][word[i+4]] += 1

            i = len(word) - 4
            if len(word) == 2:
                bigram[len(word)][word[0]][word[1]] += 1
            elif len(word) == 3:
                bigram[len(word)][word[0]][word[1]] += 1
                bigram[len(word)][word[1]][word[2]] += 1
                trigram[word[0]][word[1]][word[2]] += 1
            elif len(word) >= 4:
                bigram[len(word)][word[i]][word[i+1]] += 1
                bigram[len(word)][word[i+1]][word[i+2]] += 1
                bigram[len(word)][word[i+2]][word[i+3]] += 1
                trigram[word[i]][word[i+1]][word[i+2]] += 1
                trigram[word[i+1]][word[i+2]][word[i+3]] += 1
                fourgram[word[i]][word[i+1]][word[i+2]][word[i+3]] += 1
            for letter in set(word):
                unigram[len(word)][letter] += 1

        return unigram, bigram, trigram, fourgram, fivegram

    def build_enhanced_lstm_model(self, words):
        chars = sorted(list(set(''.join(words) + '0')))
        char_to_int = {c: i for i, c in enumerate(chars)}
        int_to_char = {i: c for c, i in char_to_int.items()}

        sequences, next_letters = [], []
        for word in words:
            encoded_word = [char_to_int[char] for char in word]
            for i in range(5, len(word)):
                sequences.append(encoded_word[i-5:i])
                next_letters.append(encoded_word[i])

        sequences = pad_sequences(sequences, maxlen=5, padding='pre')
        next_letters = to_categorical(next_letters, num_classes=len(chars))

        model = Sequential()
        model.add(Embedding(input_dim=len(chars), output_dim=128))
        model.add(Conv1D(filters=128, kernel_size=3, padding='same', activation='relu'))
        model.add(Bidirectional(LSTM(256, return_sequences=False)))
        model.add(Dropout(0.4))
        model.add(Dense(len(chars), activation='softmax'))
        model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

        model.fit(sequences, next_letters, epochs=20, batch_size=256, validation_split=0.2)
        return char_to_int, int_to_char, model

    def guess(self, word):
        clean_word = word[::2]
        self.incorrect_guesses = set(self.guessed_letters) - set(word)

        if self.guessed_letters and self.guessed_letters[-1] in self.incorrect_guesses:
            self.reoptimize_ngrams()

        self.probabilities = [0] * len(self.letter_set)

        # Use each n-gram model in sequence
        predicted_letter = self.fivegram_probability(clean_word)
        if predicted_letter in self.guessed_letters or not predicted_letter:
            predicted_letter = self.fourgram_probability(clean_word)
        if predicted_letter in self.guessed_letters or not predicted_letter:
            predicted_letter = self.trigram_probability(clean_word)
        if predicted_letter in self.guessed_letters or not predicted_letter:
            predicted_letter = self.bigram_probability(clean_word)
        if predicted_letter in self.guessed_letters or not predicted_letter:
            predicted_letter = self.unigram_probability(clean_word)

        # Ensure the predicted letter is not one of the incorrect guesses
        while predicted_letter in self.guessed_letters:
            predicted_letter = self.next_best_letter()

        return predicted_letter

    def fivegram_probability(self, word):
        probs = [0] * len(self.letter_set)
        total_count = 0
        letter_count = [0] * len(self.letter_set)

        for i in range(len(word) - 4):
            if word[i] != '_' and word[i+1] != '_' and word[i+2] != '_' and word[i+3] != '_' and word[i+4] == '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+1]
                anchor_letter3 = word[i+2]
                anchor_letter4 = word[i+3]

                for j, letter in enumerate(self.letter_set):
                    if self.fivegram[anchor_letter1][anchor_letter2][anchor_letter3][anchor_letter4][letter] > 0 and letter not in self.guessed_letters:
                        total_count += self.fivegram[anchor_letter1][anchor_letter2][anchor_letter3][anchor_letter4][letter]
                        letter_count[j] += self.fivegram[anchor_letter1][anchor_letter2][anchor_letter3][anchor_letter4][letter]

            elif word[i] != '_' and word[i+1] != '_' and word[i+2] != '_' and word[i+3] == '_' and word[i+4] != '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+1]
                anchor_letter3 = word[i+2]
                anchor_letter4 = word[i+4]

                for j, letter in enumerate(self.letter_set):
                    if self.fivegram[anchor_letter1][anchor_letter2][anchor_letter3][letter][anchor_letter4] > 0 and letter not in self.guessed_letters:
                        total_count += self.fivegram[anchor_letter1][anchor_letter2][anchor_letter3][letter][anchor_letter4]
                        letter_count[j] += self.fivegram[anchor_letter1][anchor_letter2][anchor_letter3][letter][anchor_letter4]

            elif word[i] != '_' and word[i+1] != '_' and word[i+2] == '_' and word[i+3] != '_' and word[i+4] != '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+1]
                anchor_letter3 = word[i+3]
                anchor_letter4 = word[i+4]

                for j, letter in enumerate(self.letter_set):
                    if self.fivegram[anchor_letter1][anchor_letter2][letter][anchor_letter3][anchor_letter4] > 0 and letter not in self.guessed_letters:
                        total_count += self.fivegram[anchor_letter1][anchor_letter2][letter][anchor_letter3][anchor_letter4]
                        letter_count[j] += self.fivegram[anchor_letter1][anchor_letter2][letter][anchor_letter3][anchor_letter4]

            elif word[i] != '_' and word[i+1] == '_' and word[i+2] != '_' and word[i+3] != '_' and word[i+4] != '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+2]
                anchor_letter3 = word[i+3]
                anchor_letter4 = word[i+4]

                for j, letter in enumerate(self.letter_set):
                    if self.fivegram[anchor_letter1][letter][anchor_letter2][anchor_letter3][anchor_letter4] > 0 and letter not in self.guessed_letters:
                        total_count += self.fivegram[anchor_letter1][letter][anchor_letter2][anchor_letter3][anchor_letter4]
                        letter_count[j] += self.fivegram[anchor_letter1][letter][anchor_letter2][anchor_letter3][anchor_letter4]

            elif word[i] == '_' and word[i+1] != '_' and word[i+2] != '_' and word[i+3] != '_' and word[i+4] != '_':
                anchor_letter1 = word[i+1]
                anchor_letter2 = word[i+2]
                anchor_letter3 = word[i+3]
                anchor_letter4 = word[i+4]

                for j, letter in enumerate(self.letter_set):
                    if self.fivegram[letter][anchor_letter1][anchor_letter2][anchor_letter3][anchor_letter4] > 0 and letter not in self.guessed_letters:
                        total_count += self.fivegram[letter][anchor_letter1][anchor_letter2][anchor_letter3][anchor_letter4]
                        letter_count[j] += self.fivegram[letter][anchor_letter1][anchor_letter2][anchor_letter3][anchor_letter4]

        if total_count > 0:
            for i in range(len(self.letter_set)):
                probs[i] = letter_count[i] / total_count

        blanks_remaining = word.count('_')
        adaptive_weight = 0.40 + (0.05 * blanks_remaining)

        for i, p in enumerate(self.probabilities):
            self.probabilities[i] = p + probs[i] * adaptive_weight

        return self.select_best_letter()

    def fourgram_probability(self, word):
        probs = [0] * len(self.letter_set)
        total_count = 0
        letter_count = [0] * len(self.letter_set)

        for i in range(len(word) - 3):
            if word[i] != '_' and word[i+1] != '_' and word[i+2] != '_' and word[i+3] == '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+1]
                anchor_letter3 = word[i+2]

                for j, letter in enumerate(self.letter_set):
                    if self.fourgram[anchor_letter1][anchor_letter2][anchor_letter3][letter] > 0 and letter not in self.guessed_letters:
                        total_count += self.fourgram[anchor_letter1][anchor_letter2][anchor_letter3][letter]
                        letter_count[j] += self.fourgram[anchor_letter1][anchor_letter2][anchor_letter3][letter]

            elif word[i] != '_' and word[i+1] != '_' and word[i+2] == '_' and word[i+3] != '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+1]
                anchor_letter3 = word[i+3]

                for j, letter in enumerate(self.letter_set):
                    if self.fourgram[anchor_letter1][anchor_letter2][letter][anchor_letter3] > 0 and letter not in self.guessed_letters:
                        total_count += self.fourgram[anchor_letter1][anchor_letter2][letter][anchor_letter3]
                        letter_count[j] += self.fourgram[anchor_letter1][anchor_letter2][letter][anchor_letter3]

            elif word[i] != '_' and word[i+1] == '_' and word[i+2] != '_' and word[i+3] != '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+2]
                anchor_letter3 = word[i+3]

                for j, letter in enumerate(self.letter_set):
                    if self.fourgram[anchor_letter1][letter][anchor_letter2][anchor_letter3] > 0 and letter not in self.guessed_letters:
                        total_count += self.fourgram[anchor_letter1][letter][anchor_letter2][anchor_letter3]
                        letter_count[j] += self.fourgram[anchor_letter1][letter][anchor_letter2][anchor_letter3]

            elif word[i] == '_' and word[i+1] != '_' and word[i+2] != '_' and word[i+3] != '_':
                anchor_letter1 = word[i+1]
                anchor_letter2 = word[i+2]
                anchor_letter3 = word[i+3]

                for j, letter in enumerate(self.letter_set):
                    if self.fourgram[letter][anchor_letter1][anchor_letter2][anchor_letter3] > 0 and letter not in self.guessed_letters:
                        total_count += self.fourgram[letter][anchor_letter1][anchor_letter2][anchor_letter3]
                        letter_count[j] += self.fourgram[letter][anchor_letter1][anchor_letter2][anchor_letter3]

        if total_count > 0:
            for i in range(len(self.letter_set)):
                probs[i] = letter_count[i] / total_count

        blanks_remaining = word.count('_')
        adaptive_weight = 0.30 + (0.03 * blanks_remaining)

        for i, p in enumerate(self.probabilities):
            self.probabilities[i] = p + probs[i] * adaptive_weight

        return self.select_best_letter()

    def trigram_probability(self, word):
        probs = [0] * len(self.letter_set)
        total_count = 0
        letter_count = [0] * len(self.letter_set)

        for i in range(len(word) - 2):
            if word[i] != '_' and word[i+1] != '_' and word[i+2] == '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+1]

                for j, letter in enumerate(self.letter_set):
                    if self.trigram[anchor_letter1][anchor_letter2][letter] > 0 and letter not in self.guessed_letters:
                        total_count += self.trigram[anchor_letter1][anchor_letter2][letter]
                        letter_count[j] += self.trigram[anchor_letter1][anchor_letter2][letter]

            elif word[i] != '_' and word[i+1] == '_' and word[i+2] != '_':
                anchor_letter1 = word[i]
                anchor_letter2 = word[i+2]

                for j, letter in enumerate(self.letter_set):
                    if self.trigram[anchor_letter1][letter][anchor_letter2] > 0 and letter not in self.guessed_letters:
                        total_count += self.trigram[anchor_letter1][letter][anchor_letter2]
                        letter_count[j] += self.trigram[anchor_letter1][letter][anchor_letter2]

            elif word[i] == '_' and word[i+1] != '_' and word[i+2] != '_':
                anchor_letter1 = word[i+1]
                anchor_letter2 = word[i+2]

                for j, letter in enumerate(self.letter_set):
                    if self.trigram[letter][anchor_letter1][anchor_letter2] > 0 and letter not in self.guessed_letters:
                        total_count += self.trigram[letter][anchor_letter1][anchor_letter2]
                        letter_count[j] += self.trigram[letter][anchor_letter1][anchor_letter2]

        if total_count > 0:
            for i in range(len(self.letter_set)):
                probs[i] = letter_count[i] / total_count

        blanks_remaining = word.count('_')
        adaptive_weight = 0.20 + (0.02 * blanks_remaining)

        for i, p in enumerate(self.probabilities):
            self.probabilities[i] = p + probs[i] * adaptive_weight

        return self.select_best_letter()

    def bigram_probability(self, word):
        probs = [0] * len(self.letter_set)
        total_count = 0
        letter_count = [0] * len(self.letter_set)

        for i in range(len(word) - 1):
            if word[i] != '_' and word[i+1] == '_':
                anchor_letter = word[i]

                for j, letter in enumerate(self.letter_set):
                    if self.bigram[len(word)][anchor_letter][letter] > 0 and letter not in self.guessed_letters:
                        total_count += self.bigram[len(word)][anchor_letter][letter]
                        letter_count[j] += self.bigram[len(word)][anchor_letter][letter]

            elif word[i] == '_' and word[i+1] != '_':
                anchor_letter = word[i+1]

                for j, letter in enumerate(self.letter_set):
                    if self.bigram[len(word)][letter][anchor_letter] > 0 and letter not in self.guessed_letters:
                        total_count += self.bigram[len(word)][letter][anchor_letter]
                        letter_count[j] += self.bigram[len(word)][letter][anchor_letter]

        if total_count > 0:
            for i in range(len(self.letter_set)):
                probs[i] = letter_count[i] / total_count

        blanks_remaining = word.count('_')
        adaptive_weight = 0.10 + (0.01 * blanks_remaining)

        for i, p in enumerate(self.probabilities):
            self.probabilities[i] = p + probs[i] * adaptive_weight

        return self.select_best_letter()

    def unigram_probability(self, word):
        probs = [0] * len(self.letter_set)
        total_count = 0
        letter_count = [0] * len(self.letter_set)

        for i in range(len(word)):
            if word[i] == '_':
                for j, letter in enumerate(self.letter_set):
                    if self.unigram[len(word)][letter] > 0 and letter not in self.guessed_letters:
                        total_count += self.unigram[len(word)][letter]
                        letter_count[j] += self.unigram[len(word)][letter]

        if total_count > 0:
            for i in range(len(self.letter_set)):
                probs[i] = letter_count[i] / total_count

        for i, p in enumerate(self.probabilities):
            self.probabilities[i] = p + probs[i] * 0.05

        return self.select_best_letter()

    def select_best_letter(self):
        max_prob = 0
        guess_letter = ''
        for i, letter in enumerate(self.letter_set):
            if self.probabilities[i] > max_prob and letter not in self.guessed_letters and letter not in self.incorrect_guesses:
                max_prob = self.probabilities[i]
                guess_letter = letter

        if guess_letter == '':
            # Fallback to the most common letters in the dictionary
            sorted_letter_count = self.full_dictionary_common_letter_sorted
            for letter, instance_count in sorted_letter_count:
                if letter not in self.guessed_letters and letter not in self.incorrect_guesses:
                    return letter

        return guess_letter


    def next_best_letter(self):
        available_letters = [letter for letter in self.letter_set if letter not in self.guessed_letters]

        if not available_letters:
            return np.random.choice(self.letter_set)

        padded_sequence = pad_sequences([self.guessed_letters], maxlen=5, padding='pre')
        probs = self.model.predict(padded_sequence)[0]

        return max(available_letters, key=lambda l: probs[self.char_to_int[l]])

    def predict_next_letter_lstm(self, word):
        encoded_word = [self.char_to_int.get(char, self.char_to_int['0']) for char in word if char != '_']
        padded_sequence = pad_sequences([encoded_word], maxlen=5, padding='pre')
        probs = self.model.predict(padded_sequence)[0]
        return self.letter_set[np.argmax(probs)]

    def reoptimize_ngrams(self):
        new_dictionary = [word for word in self.full_dictionary if not set(word).intersection(self.incorrect_guesses)]
        self.unigram, self.bigram, self.trigram, self.fourgram, self.fivegram = self.build_ngram_models(new_dictionary)

    def start_game(self, practice=True, verbose=True):
        self.guessed_letters = []
        self.current_dictionary = self.full_dictionary

        response = self.request("/new_game", {"practice": practice})
        if response.get('status') == "approved":
            game_id = response.get('game_id')
            word = response.get('word')
            tries_remains = response.get('tries_remains')
            if verbose:
                print(f"Successfully started a new game! Game ID: {game_id}. # of tries remaining: {tries_remains}. Word: {word}.")
            while tries_remains > 0:
                guess_letter = self.guess(word)
                self.guessed_letters.append(guess_letter)
                if verbose:
                    print(f"Guessing letter: {guess_letter}")

                try:
                    res = self.request("/guess_letter", {"request": "guess_letter", "game_id": game_id, "letter": guess_letter})
                except HangmanAPIError:
                    print('HangmanAPIError exception caught on request.')
                    continue
                except Exception as e:
                    print('Other exception caught on request.')
                    raise e

                if verbose:
                    print(f"Server response: {res}")
                status = res.get('status')
                tries_remains = res.get('tries_remains')
                if status == "success":
                    if verbose:
                        print(f"Successfully finished game: {game_id}")
                    return True
                elif status == "failed":
                    reason = res.get('reason', '# of tries exceeded!')
                    if verbose:
                        print(f"Failed game: {game_id}. Because of: {reason}")
                    return False
                elif status == "ongoing":
                    word = res.get('word')
        else:
            if verbose:
                print("Failed to start a new game")
        return status == "success"

    def my_status(self):
        return self.request("/my_status", {})

    def request(self, path, args=None, post_args=None, method=None):
        if args is None:
            args = dict()
        if post_args is not None:
            method = "POST"

        if self.access_token:
            if post_args and "access_token" not in post_args:
                post_args["access_token"] = self.access_token
            elif "access_token" not in args:
                args["access_token"] = self.access_token

        time.sleep(0.2)

        num_retry, time_sleep = 50, 2
        for it in range(num_retry):
            try:
                response = self.session.request(
                    method or "GET",
                    self.hangman_url + path,
                    timeout=self.timeout,
                    params=args,
                    data=post_args,
                    verify=False
                )
                break
            except requests.HTTPError as e:
                response = json.loads(e.read())
                raise HangmanAPIError(response)
            except requests.exceptions.SSLError as e:
                if it + 1 == num_retry:
                    raise
                time.sleep(time_sleep)

        headers = response.headers
        if 'json' in headers['content-type']:
            result = response.json()
        elif "access_token" in parse_qs(response.text):
            query_str = parse_qs(response.text)
            if "access_token" in query_str:
                result = {"access_token": query_str["access_token"][0]}
                if "expires" in query_str:
                    result["expires"] = query_str["expires"][0]
            else:
                raise HangmanAPIError(response.json())
        else:
            raise HangmanAPIError('Maintype was not text, or querystring')

        if result and isinstance(result, dict) and result.get("error"):
            raise HangmanAPIError(result)
        return result

class HangmanAPIError(Exception):
    def __init__(self, result):
        self.result = result
        self.code = None
        try:
            self.type = result["error_code"]
        except (KeyError, TypeError):
            self.type = ""
        try:
            self.message = result["error_description"]
        except (KeyError, TypeError):
            try:
                self.message = result["error"]["message"]
                self.code = result["error"].get("code")
                if not self.type:
                    self.type = result["error"].get("type", "")
            except (KeyError, TypeError):
                try:
                    self.message = result["error_msg"]
                except (KeyError, TypeError):
                    self.message = result
        Exception.__init__(self, self.message)



In [15]:

# Instantiate and run the HangmanAPI
api = HangmanAPI(access_token="a508b6d8bf1e0d00a5b3f8dd331355", timeout=2000)


Epoch 1/20
3122/3122 ━━━━━━━━━━━━━━━━━━━━ 29s 8ms/step - accuracy: 0.2862 - loss: 2.2732 - val_accuracy: 0.4003 - val_loss: 1.8969
Epoch 2/20
3122/3122 ━━━━━━━━━━━━━━━━━━━━ 26s 8ms/step - accuracy: 0.4056 - loss: 1.8614 - val_accuracy: 0.4337 - val_loss: 1.8036
Epoch 3/20
3122/3122 ━━━━━━━━━━━━━━━━━━━━ 26s 8ms/step - accuracy: 0.4411 - loss: 1.7496 - val_accuracy: 0.4483 - val_loss: 1.7597
Epoch 4/20
3122/3122 ━━━━━━━━━━━━━━━━━━━━ 41s 8ms/step - accuracy: 0.4623 - loss: 1.6827 - val_accuracy: 0.4586 - val_loss: 1.7318
Epoch 5/20
3122/3122 ━━━━━━━━━━━━━━━━━━━━ 26s 8ms/step - accuracy: 0.4762 - loss: 1.6319 - val_accuracy: 0.4638 - val_loss: 1.7193
Epoch 6/20
3122/3122 ━━━━━━━━━━━━━━━━━━━━ 26s 8ms/step - accuracy: 0.4878 - loss: 1.5923 - val_accuracy: 0.4665 - val_loss: 1.7094
Epoch 7/20
3122/3122 ━━━━━━━━━━━━━━━━━━━━ 26s 8ms/step - accuracy: 0.4966 - loss: 1.5642 - val_accuracy: 0.4722 - val_loss: 1.6982
Epoch 8/20
3122/3122 ━━━━━━━━━━━━━━━━━━━━ 41s 8ms/step - accuracy: 0.5041 - loss: 1

In [16]:

api.start_game(practice=1, verbose=True)
status = api.my_status()
if status:
    [total_practice_runs, total_recorded_runs, total_recorded_successes, total_practice_successes] = status
    practice_success_rate = total_practice_successes / total_practice_runs
    print('Run %d practice games out of an allotted 100,000. Practice success rate so far = %.3f' % (total_practice_runs, practice_success_rate))


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Successfully started a new game! Game ID: ab012a98010c. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ _ _ .
Guessing letter: e


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Server response: {'game_id': 'ab012a98010c', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ _ _ _ _ _ '}
Guessing letter: i


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


...

/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Server response: {'game_id': 'ab012a98010c', 'status': 'ongoing', 'tries_remains': 3, 'word': 'c a l i _ r a t i o n s '}
Guessing letter: b


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Server response: {'game_id': 'ab012a98010c', 'status': 'success', 'tries_remains': 3, 'word': 'c a l i b r a t i o n s '}
Successfully finished game: ab012a98010c
Run 631 practice games out of an allotted 100,000. Practice success rate so far = 0.377


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


In [13]:
for i in range(10):
    print(f'Playing {i + 1}th game')
    api.start_game(practice=1, verbose=True)
    time.sleep(0.5)

Playing 1th game


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Successfully started a new game! Game ID: f901ad7b0114. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ _ .
Guessing letter: e


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Server response: {'game_id': 'f901ad7b0114', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ e _ _ _ _ _ _ _ _ '}
Guessing letter: i


...

Server response: {'game_id': 'b681e309bf79', 'status': 'ongoing', 'tries_remains': 3, 'word': 't r i c h o _ h _ t o s i s '}
Guessing letter: p


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Server response: {'game_id': 'b681e309bf79', 'status': 'ongoing', 'tries_remains': 3, 'word': 't r i c h o p h _ t o s i s '}
Guessing letter: y


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Server response: {'game_id': 'b681e309bf79', 'status': 'success', 'tries_remains': 3, 'word': 't r i c h o p h y t o s i s '}
Successfully finished game: b681e309bf79


In [20]:
for i in range(1000):
    print('Playing ', i, ' th game')
    api.start_game(practice=0,verbose=False)

    # DO NOT REMOVE as otherwise the server may lock you out for too high frequency of requests
    time.sleep(0.5)

Playing  0  th game


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: Insecur

Playing  1  th game


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: Insecur

Playing  2  th game


...

Playing  975  th game


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: Insecur

Playing  976  th game


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


HangmanAPIError: {'error': 'You have reached 1000 of games', 'status': 'denied'}

In [19]:
[total_practice_runs,total_recorded_runs,total_recorded_successes,total_practice_successes] = api.my_status() # Get my game stats: (# of tries, # of wins)
success_rate = total_recorded_successes/total_recorded_runs
print('overall success rate = %.3f' % success_rate)

overall success rate = 0.522


/usr/local/lib/python3.10/dist-packages/urllib3/connectionpool.py:1100: InsecureRequestWarning: Unverified HTTPS request is being made to host 'trexsim.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
